In [1]:
import networkx as nx
import numpy as np
import matplotlib.pyplot as plt 
import pdb

# The idea of simulation: Seeds = Nodes and Tiles/Tube = Edges
# All possible joining events will be considered and K join will be calculated.
# instead of designating "species" this algorithm will explicitly account for all structures in the system
# all possible joining events will be considered and their rates calculated, then the gillespie algorithm can be applied
# Then the simulation will be applied.
# The simulation is based on the Gillespie algorithm to track all possible structures in the system.
# https://en.wikipedia.org/wiki/Gillespie_algorithm

# Also, the code will be used to compute the largest network for each joining event

# There are few assumptions for builiding the computational model.
# 1. There are six types of seeds:
# A seeds with 1,2,and 3 arms
# B seeds with 1,2,and 3 arms

# 2. There is a certain condition fulfilled for joining to occur: 
# Joining can only occur if there is open end (# of connected edge < # of attachment site) 
# and two coming seeds should have different adapter type (A or B)
# Network joining will occur by adding an edge between two tube ends 
# (that is, an edge between two nodes that both have arms>connections)

# 3. The number of different types of seeds aer set based on the experimental data 
# and to fit experimental data

# 4. The maximum/final time being printed out for simulation is approximately 23 hours.
# This is set based on the experimental timeline.

class JoiningEvent:
# This will enable us to track the largest network at each joining event
# We do this by finding out the larger and shorter parent network
# If A has 10 nodes and B has 20 nodes in the subgraph
# And as they form a new network A-B, larger parent network is A

    def __init__(self, parent_network_1, parent_network_2):
        self.p1 = parent_network_1
        self.p2 = parent_network_2
        self.lowest_node_1 = min(parent_network_1.nodes())
        self.lowest_node_2 = min(parent_network_2.nodes())
        self.p1_size = parent_network_1.number_of_nodes()
        self.p2_size = parent_network_2.number_of_nodes()
        self.p1_short_path = nx.average_shortest_path_length(parent_network_1)
        self.p2_short_path = nx.average_shortest_path_length(parent_network_2)


    def larger_parent(self):
        if self.p1.number_of_nodes() >= self.p2.number_of_nodes():
            return self.lowest_node_1
        else: 
            return self.lowest_node_2

    def short_path(self):
        if self.p1.number_of_nodes() >= self.p2.number_of_nodes():
            return self.p1_short_path
        else: 
            return self.p2_short_path

def initialize_system(n_mult):
# This function will initialize system by setting up initial conditions and node attributes
# Node attributes include information about the Y-shaped seed:
# adapter type (A or B) and arm size (1,2,and 3)
# System will be one giant graph and connected_component_subgraphs will be used to identify individual species

# The ratio of 1 armed, 2 armed, and 3 armed are based on the experimental observation
# We averaged positive (12:42:46) and negative (10:36:54) 
# Use constant 3.86E6
    # Total number of seeds is n_mult*200
   
    system = nx.Graph()
    n_1arm_a = 12*n_mult
    n_2arm_a = 42*n_mult
    n_3arm_a = 46*n_mult
    a_seeds = (n_1arm_a+n_2arm_a+n_3arm_a)

    n_1arm_b = 10*n_mult
    n_2arm_b = 36*n_mult
    n_3arm_b = 54*n_mult
    b_seeds = (n_1arm_b+n_2arm_b+n_3arm_b)

    
    for i in range(n_1arm_a):
        system.add_node(system.number_of_nodes()+1, arms = 1, adapter = 'A', parent1 = 'null', parent2 = 'null')
    for i in range(n_2arm_a):
        system.add_node(system.number_of_nodes()+1, arms = 2, adapter = 'A', parent1 = 'null', parent2 = 'null')
    for i in range(n_3arm_a):
        system.add_node(system.number_of_nodes()+1, arms = 3, adapter = 'A', parent1 = 'null', parent2 = 'null')

    for i in range(n_1arm_b):
        system.add_node(system.number_of_nodes()+1, arms = 1, adapter = 'B', parent1 = 'null', parent2 = 'null')
    for i in range(n_2arm_b):
        system.add_node(system.number_of_nodes()+1, arms = 2, adapter = 'B', parent1 = 'null', parent2 = 'null')
    for i in range(n_3arm_b):
        system.add_node(system.number_of_nodes()+1, arms = 3, adapter = 'B', parent1 = 'null', parent2 = 'null')

    print ("Number of positive seeds being simulated:", a_seeds)
    print ("Number of negative seeds being simulated:", b_seeds)
    
    return system

def compute_rtot_first(system):
# This function calculates total reaction rate
# Total reaction rate is calculated by computing joining reaction rate for each reaction and sum all reaction rates
# In order to do this, we need to create all subgraphs. Then we calculate joining rate for all possible subgraph joining and add all joining rates
    
    graphs = [system.subgraph(c) for c in nx.connected_components(system)]
   
    rtot = 0
    
    for i in range(len(graphs)):
        for j in range (i+1, len(graphs)):
            network_1 = graphs[i]
            network_2 = graphs[j]
            kjoin = joining_rate(network_1, network_2)
            rtot += kjoin
            print (kjoin)

    return rtot 


def update_rtot(old_rtot, network_1, network_2, new_network, system_old):
# The objective of this function is to update r total
# When a joining event occurs rtot is reduced because there is one less possible reaction
# Thus, the joining events corresponding to joining with either of the partners are eliminated and a new set of joining events for joining to the new network are added  
# As shown in def joining_event, network_1 and network_2 join to make new_network
# For instance, A-B is network_1, C-D is network_2 and A-B-C-D is new_network
# Let's say system_old is A-B, C-D, E,F
# To update r total, we first generate all subgraphs from the previous system 
# Then we subtract all joining rate terms associated with either network_1 or network_2
# Now, add all joining rate terms for joining event between new_network (A-B-C-D) and lists of subgraphs excluding network_1, network_2, or new_network
    
    graphs = [system.subgraph(c) for c in nx.connected_components(system_old)]
    
    rtot = old_rtot
    
    for i in range(len(graphs)):
        network = graphs[i]
        
        kjoin1 = joining_rate(network_1, network)
        rtot -= kjoin1
        
        kjoin2 = joining_rate(network_2, network)
        rtot -= kjoin2
        
        kjoin_new = joining_rate(new_network, network)
        rtot+=kjoin_new 

    print (rtot) 
    return rtot 

def joining_rate(network_1, network_2):
# Now, we need to compute the joining rates 
# This function computes joining rate by considering the possible joinig points for two different networks
# Instead of calculating joining rates for all possible pairs every time, we update total reaction rate and recation possibilites. 
# When the joining occurs, K_total value will be decreased, because there is one less possible reaction
# The joining events corresponding to joining with either of the partners are eliminated
# Then a new set of joining events for joining to the new network are added 
# The model will return 0 if the two networks are not joined
# There is a condition that should be fulfilled for joining to occur (as mentioned above)
# As mentioned above,arms have different arm size and two types of seeds
    # The attachment can only occur if there is a free end (number of edges < available ) and joining seeds have different type
    
    connectivity_dict1 = nx.get_node_attributes(network_1, 'arms')
    adapter_dict1 = nx.get_node_attributes(network_1, 'adapter')
    connectivity_dict2 = nx.get_node_attributes(network_2, 'arms')
    adapter_dict2 = nx.get_node_attributes(network_2, 'adapter')

    valid_positive_attachment_points_1 = 0
    valid_negative_attachment_points_1 = 0
    
    for node, narms in connectivity_dict1.items():
        if network_1.degree(node) < narms and network_1.nodes[node]['adapter'] == 'A':
            valid_positive_attachment_points_1 += narms - network_1.degree(node)
        if network_1.degree(node) < narms and network_1.nodes[node]['adapter'] == 'B':
            valid_negative_attachment_points_1 += narms - network_1.degree(node)

    valid_positive_attachment_points_2 = 0
    valid_negative_attachment_points_2 = 0

    for node, narms in connectivity_dict2.items():
        if network_2.degree(node) < narms and network_2.nodes[node]['adapter'] == 'A':
            valid_positive_attachment_points_2 += narms - network_2.degree(node)
        if network_2.degree(node) < narms and network_2.nodes[node]['adapter'] == 'B':
            valid_negative_attachment_points_2 += narms - network_2.degree(node)
    
    number_of_possible_connections = float(valid_positive_attachment_points_1*valid_negative_attachment_points_2 + valid_negative_attachment_points_1*valid_positive_attachment_points_2)
    kjoin = 1.0

    return kjoin*number_of_possible_connections

def compute_dt(rtot):
# Compute dt from total reaction rate
# Time-to-the-next-jump is exponentially distributed according to the Gillespie algorith
# and the probability of the next event is proportional to the rate.
    
    dt = np.random.exponential(float(1.0/rtot))
    
    return dt

def choose_joining_reaction(rtot, system, joining_matrix, joining_matrix_index_dictionary):
# Now, intra-network joining reactions are being computed
# we choose a joining reaction with probabilites = reaction rate/rtot
# First, we produce list of all connected subgraphs
# Then, probabilities for all pairwise joining reactions will be computed
# Then the joining matrix indices are used as dictionary

    graphs = [system.subgraph(c) for c in nx.connected_components(system)]
    print ("Previous number of connected graphs", len(graphs))

    pairwise_probabilities = joining_matrix.ravel()/np.sum(joining_matrix)
    ravel_indices = []
    for i in range(len(pairwise_probabilities)):
        ravel_indices.append(i)

    chosen_ravel_index = np.random.choice(ravel_indices, p = pairwise_probabilities)
    chosen_matrix_indices = np.unravel_index(chosen_ravel_index, joining_matrix.shape)

    index_of_network_1 = chosen_matrix_indices[0]
    index_of_network_2 = chosen_matrix_indices[1]
    lowest_node_in_network_1 = joining_matrix_index_dictionary[index_of_network_1]
    lowest_node_in_network_2 = joining_matrix_index_dictionary[index_of_network_2]

    for network in graphs:
        if network.has_node(lowest_node_in_network_1):
            network_1 = network
            break
            
    for network in graphs:
        if network.has_node(lowest_node_in_network_2):
            network_2 = network
            break

    return network_1, network_2, index_of_network_1, index_of_network_2

def perform_joining(network_1, network_2, system):
# Now, we perform joining by adding edge between network 1 and network 2
# Random addition of edges, but there is a condition to be fulfilled to add edges:
# Edges are connected if there is an open and coming seed is active

    joining_event = JoiningEvent(network_1, network_2)
    
    connectivity_dict1 = nx.get_node_attributes(network_1, 'arms')
    connectivity_dict2 = nx.get_node_attributes(network_2, 'arms')
    valid_connection = False
    
    while valid_connection == False: 
        network_1_node = np.random.choice(network_1.nodes())
        network_2_node = np.random.choice(network_2.nodes())
        network_1_node_narms = connectivity_dict1[network_1_node]
        network_2_node_narms = connectivity_dict2[network_2_node]
        
        if network_1.degree(network_1_node) < network_1_node_narms and network_2.degree(network_2_node) < network_2_node_narms and network_1.nodes[network_1_node]['adapter'] != network_2.nodes[network_2_node]['adapter'] :
            #print ("Adding valid connection")
            valid_connection = True
    system.add_edge(network_1_node, network_2_node)
    new_network = nx.union(network_1, network_2)
    new_network.add_edge(network_1_node, network_2_node)

    return system, new_network, joining_event

def initialize_joining_matrix(system):
# We need to initialize joining matrix (# nodes in the system x # nodes in the system)
# This matrix takes inter-network joining into account
# Each matrix element is calculated by pairwise joining rates for all nodes
# The matrix will be symmetric since joining rate for network1-2 is the same for that of network2-1
# Also, diagonal elements will be zero (cannot join by itself). So we will generate/store upper diagonal
# We first find the minimum node number in the graph
# Then create dictionary with index in the joining matrix with a network. 
# Key will be the node number

    joining_matrix = np.zeros((system.number_of_nodes(),system.number_of_nodes()))
    graphs = [system.subgraph(c) for c in nx.connected_components(system)]
    joining_matrix_index_dictionary = {}
    
    for i in range(len(graphs)):
        if i%25 == 0:
            print('initting graph '+ str(i))
        lowest_node_number = min(graphs[i].nodes())
        joining_matrix_index_dictionary[i] = lowest_node_number 
        for j in range (i+1, len(graphs)):
            network_1 = graphs[i]
            network_2 = graphs[j]
            kjoin = joining_rate(network_1, network_2)
            joining_matrix[i,j] = kjoin 
            # Now we have joining matrix that contains k join, which is the joining rate when ith and jth subgraphs are joint
   
    return joining_matrix, joining_matrix_index_dictionary

def compute_rtot_from_joining_matrix(joining_matrix):
# Computes rtot from the initial joining matrix by summing all elements in the matrix
    
    matrix_sum = np.sum(joining_matrix)

    return matrix_sum

def update_joining_matrix(joining_matrix, joining_matrix_index_dictionary, joined_network_1, joined_network_2, new_network, index_1, index_2, system):
# This function is used to update joining matrix and dictionary once two networks (network1 and network 2) are joint
# First, we find the lowest number of node for each network
# This will be used to find elements of joining matrix to edit
# We then remove row and column associated with network 1 and 2
# For indices that are lower than index 1 or 2, thery are not affected by the previous joining, so they will remain
# If indices are larger than index 1, they are decreased by 1 as they are affected by deletion

    lowest_node_1 = min(joined_network_1.nodes())
    lowest_node_2 = min(joined_network_2.nodes())

    joining_matrix = np.delete(joining_matrix, index_1, 0) 
    joining_matrix = np.delete(joining_matrix, index_1, 1) 

    updated_dict_1 = {}
    
    for key, value in joining_matrix_index_dictionary.items():
        if key< index_1:
            updated_dict_1[key] = value 
        if key> index_1:
            new_key = key - 1
            updated_dict_1[new_key] = value

    if index_2>index_1:
        index_2-=1

    joining_matrix = np.delete(joining_matrix, index_2, 0)
    joining_matrix = np.delete(joining_matrix, index_2, 1) 

    updated_dict_2 = {}
    
    for key, value in updated_dict_1.items():
        if key< index_2:
            updated_dict_2[key] = value 
        if key> index_2:
            new_key = key - 1
            updated_dict_2[new_key] = value

# Now we will add a row and column for the new network that was created by the joining event
# This will be inserted to the rightmost column and bottommost row
# This can be done by firstly adding a column of zeroes on the right and row of zeroes on the bottom

    new_column = np.zeros(np.size(joining_matrix,1))
    joining_matrix = np.insert(joining_matrix,np.size(joining_matrix,1),new_column, axis=1)

    new_row = np.zeros(np.size(joining_matrix,1))
    joining_matrix = np.insert(joining_matrix,np.size(joining_matrix,0),new_row, axis=0)
    
# Now we calculte joining rate for new network and all other networks in the system
# We will exclude reaction of new network itself by setting kjoin as 0 
# if index for network that already have been joint are used

    graphs = [system.subgraph(c) for c in nx.connected_components(system)]

    column = np.size(joining_matrix,1)-1
    new_network_lowest_node_number = min(new_network.nodes())

    for i in range(len(graphs)):
        network = graphs[i]
        lowest_node_number = min(network.nodes())
        if lowest_node_number == new_network_lowest_node_number:
            kjoin = 0
        else:
            kjoin = joining_rate(new_network, network)
            for key, value in updated_dict_2.items(): 
                if value == lowest_node_number:
                    index = key
                    break
            joining_matrix[index,column] = kjoin 

# For the final step, we will update the dictionary
    updated_dict_2_original = updated_dict_2.copy()
    updated_dict_2[column]=new_network_lowest_node_number
    joining_matrix_index_dictionary = updated_dict_2

    return joining_matrix, joining_matrix_index_dictionary

def find_largest_parent(lowest_node, joining_event_list, current_je_index):
# We will find the largest parent network 
    
    for i in range(current_je_index-1, 0, -1):
        joining_event = joining_event_list[i]
        if joining_event.lowest_node_1 == lowest_node or joining_event.lowest_node_2 == lowest_node:
            new_je_index = i
            new_lowest_node = joining_event.larger_parent()
            network_size = joining_event.p1_size + joining_event.p2_size
            shortest_path = joining_event.short_path()
            return new_je_index, new_lowest_node, network_size, shortest_path  
            break 
# If we get to here then there are no more parents!
    return 0, 0, 1, 1

def perform_gillespie_simulation(iter,n_mult,k_join_fact,data_dir):
# Now, we will run the Gillespie algorithm  

# The simulation will track average nodes per network, number of connected graphs, and time
# We will stop just short of everything in the systme are joined

    system = initialize_system(n_mult)
    joining_event_list = []


    number_of_joining_steps = system.number_of_nodes()
    average_nodes_per_network = [1]
    number_of_connected_graphs = [system.number_of_nodes()]
    average_seeds_per_network = [1]
    average_network_size_of_a_seed_list = [1]

    time = [0]

# We will then store pairwise joining probabilities and r total
# Matrix can effectively store values for the system
# We first calculate rates for inter-network joining events 

    joining_matrix, joining_matrix_index_dictionary = initialize_joining_matrix(system)
    rtot = compute_rtot_from_joining_matrix(joining_matrix)

    print ("R total before next simulation starts: ", rtot)
    
    for step in range(number_of_joining_steps):
        print ("Updated R total: ", rtot)
        if rtot == 0.0:
            print ("There is no more possible joining events that can occur.")
            break
        dt = compute_dt(rtot)
        previous_time = time[len(time)-1]
        new_time = previous_time + dt
        time.append(new_time)



# Now we now we determine which joining reaction will occur
# Based on the probability for a given reaction: joining reaction rate / rtot
        joined_network_1, joined_network_2, index_1, index_2 = choose_joining_reaction(rtot, system, joining_matrix, joining_matrix_index_dictionary)

# Once we find out which networks are involved in joining, we perfrom joining reaction by adding edges
# We also update r tot for the next iteration
        system, new_network, joining_event = perform_joining(joined_network_1, joined_network_2, system)
        joining_event_list.append(joining_event)
        new_joining_matrix, new_joining_matrix_index_dictionary = update_joining_matrix(joining_matrix, joining_matrix_index_dictionary, joined_network_1, joined_network_2, new_network, index_1, index_2, system)
        joining_matrix = new_joining_matrix
        joining_matrix_index_dictionary = new_joining_matrix_index_dictionary
        rtot_new = compute_rtot_from_joining_matrix(joining_matrix)
        rtot = rtot_new 

        graphs = [system.subgraph(c) for c in nx.connected_components(system)]
        number_of_connected_graphs.append(len(graphs))

# Average network is calculated
        network_size_count = []
        for graph in graphs:
            for node in graph.nodes():
                network_size_count.append(graph.number_of_nodes())
        average_network_size_of_a_seed = float(sum(network_size_count))/float(len(network_size_count))

        average_network_size_of_a_seed_list.append(average_network_size_of_a_seed)
        num_seeds = n_mult*100
       
        if step%1 == 0: # 
                #print ("Printing current simulation time")
                f1=open(data_dir + '/' + 'sim_' + str(iter) + '_sim_times.dat', 'a')
                print (new_time,file=f1) 
                f1.close()                        

                #print ("Printing average network size of a seed")
                f1=open(data_dir + '/' + 'sim_' + str(iter) + '_average_network_size_of_a_seed.dat','a')
                print (average_network_size_of_a_seed,file=f1)
                f1.close()

                #print ("Printing network sizes")
                f1=open(data_dir + '/' + 'sim_' + str(iter) + '_simtime_' + str(new_time)+ '_network_size_count.dat', 'w+')
                for size in network_size_count:
                    print (size,file=f1)
                f1.close()
                
# Now we will find the largest network in the joining event list and it's index 
# Then we start with the big network je index and work backward through the list, 
# And we print the largest network size at each step

    lowest_node_of_largest_network = 1
    largest_network_size = 1
    for graph in graphs:
        network_size = graph.number_of_nodes()
        if network_size > largest_network_size:
            largest_network_size = network_size
            lowest_node_of_largest_network = min(graph.nodes())
            
    for i in range(len(joining_event_list)-1, 0, -1):
        joining_event = joining_event_list[i]
        if joining_event.lowest_node_1 == lowest_node_of_largest_network or joining_event.lowest_node_2 == lowest_node_of_largest_network:
            big_network_je_index = i
            break 

    largest_network_size_list = []
    average_short_path_list = []
    big_network_je = joining_event_list[big_network_je_index]
    current_je_index = big_network_je_index
    lowest_node = big_network_je.larger_parent()

    while current_je_index > 0:
        new_je_index, new_lowest_node, network_size, average_short_path = find_largest_parent(lowest_node, joining_event_list, current_je_index)
        largest_network_size_list.append(network_size)
        average_short_path_list.append(average_short_path)
        current_je_index = new_je_index
        lowest_node = new_lowest_node

    #print ("Printing the largest network size")
    f1=open(data_dir + '/' + 'sim_' + str(iter) + '_largest_network_tracking.dat','w')
    for bn_size in largest_network_size_list:
        print (bn_size, file=f1)
    f1.close()
    


In [2]:

iters = 50
k_join_fact = 1
n_mult = 10
data_dir = 'Collected data 7_2_1155am'
for i in range(iters):
    perform_gillespie_simulation(i+1,n_mult,k_join_fact,data_dir)

Number of positive seeds being simulated: 1000
Number of negative seeds being simulated: 1000
initting graph 0
initting graph 25
initting graph 50
initting graph 75
initting graph 100
initting graph 125
initting graph 150
initting graph 175
initting graph 200
initting graph 225
initting graph 250
initting graph 275
initting graph 300
initting graph 325
initting graph 350
initting graph 375
initting graph 400
initting graph 425
initting graph 450
initting graph 475
initting graph 500
initting graph 525
initting graph 550
initting graph 575
initting graph 600
initting graph 625
initting graph 650
initting graph 675
initting graph 700
initting graph 725
initting graph 750
initting graph 775
initting graph 800
initting graph 825
initting graph 850
initting graph 875
initting graph 900
initting graph 925
initting graph 950
initting graph 975
initting graph 1000
initting graph 1025
initting graph 1050
initting graph 1075
initting graph 1100
initting graph 1125
initting graph 1150
initting gr

Updated R total:  5264307.0
Previous number of connected graphs 1905
Updated R total:  5259714.0
Previous number of connected graphs 1904
Updated R total:  5255125.0
Previous number of connected graphs 1903
Updated R total:  5250536.0
Previous number of connected graphs 1902
Updated R total:  5245949.0
Previous number of connected graphs 1901
Updated R total:  5241364.0
Previous number of connected graphs 1900
Updated R total:  5236785.0
Previous number of connected graphs 1899
Updated R total:  5232206.0
Previous number of connected graphs 1898
Updated R total:  5227629.0
Previous number of connected graphs 1897
Updated R total:  5223055.0
Previous number of connected graphs 1896
Updated R total:  5218482.0
Previous number of connected graphs 1895
Updated R total:  5213909.0
Previous number of connected graphs 1894
Updated R total:  5209340.0
Previous number of connected graphs 1893
Updated R total:  5204773.0
Previous number of connected graphs 1892
Updated R total:  5200208.0
Previo

Updated R total:  4732025.0
Previous number of connected graphs 1786
Updated R total:  4727670.0
Previous number of connected graphs 1785
Updated R total:  4723319.0
Previous number of connected graphs 1784
Updated R total:  4718974.0
Previous number of connected graphs 1783
Updated R total:  4714625.0
Previous number of connected graphs 1782
Updated R total:  4710280.0
Previous number of connected graphs 1781
Updated R total:  4705939.0
Previous number of connected graphs 1780
Updated R total:  4701598.0
Previous number of connected graphs 1779
Updated R total:  4697257.0
Previous number of connected graphs 1778
Updated R total:  4692918.0
Previous number of connected graphs 1777
Updated R total:  4688581.0
Previous number of connected graphs 1776
Updated R total:  4684251.0
Previous number of connected graphs 1775
Updated R total:  4679918.0
Previous number of connected graphs 1774
Updated R total:  4675587.0
Previous number of connected graphs 1773
Updated R total:  4671260.0
Previo

Updated R total:  4228119.0
Previous number of connected graphs 1667
Updated R total:  4224004.0
Previous number of connected graphs 1666
Updated R total:  4219891.0
Previous number of connected graphs 1665
Updated R total:  4215778.0
Previous number of connected graphs 1664
Updated R total:  4211671.0
Previous number of connected graphs 1663
Updated R total:  4207562.0
Previous number of connected graphs 1662
Updated R total:  4203457.0
Previous number of connected graphs 1661
Updated R total:  4199357.0
Previous number of connected graphs 1660
Updated R total:  4195255.0
Previous number of connected graphs 1659
Updated R total:  4191160.0
Previous number of connected graphs 1658
Updated R total:  4187061.0
Previous number of connected graphs 1657
Updated R total:  4182967.0
Previous number of connected graphs 1656
Updated R total:  4178874.0
Previous number of connected graphs 1655
Updated R total:  4174781.0
Previous number of connected graphs 1654
Updated R total:  4170690.0
Previo

Updated R total:  3752554.0
Previous number of connected graphs 1548
Updated R total:  3748679.0
Previous number of connected graphs 1547
Updated R total:  3744802.0
Previous number of connected graphs 1546
Updated R total:  3740932.0
Previous number of connected graphs 1545
Updated R total:  3737061.0
Previous number of connected graphs 1544
Updated R total:  3733195.0
Previous number of connected graphs 1543
Updated R total:  3729331.0
Previous number of connected graphs 1542
Updated R total:  3725464.0
Previous number of connected graphs 1541
Updated R total:  3721603.0
Previous number of connected graphs 1540
Updated R total:  3717745.0
Previous number of connected graphs 1539
Updated R total:  3713886.0
Previous number of connected graphs 1538
Updated R total:  3710030.0
Previous number of connected graphs 1537
Updated R total:  3706175.0
Previous number of connected graphs 1536
Updated R total:  3702322.0
Previous number of connected graphs 1535
Updated R total:  3698472.0
Previo

...

Updated R total:  956778.0
Previous number of connected graphs 591
Updated R total:  954813.0
Previous number of connected graphs 590
Updated R total:  952836.0
Previous number of connected graphs 589
Updated R total:  950876.0
Previous number of connected graphs 588
Updated R total:  948922.0
Previous number of connected graphs 587
Updated R total:  946966.0
Previous number of connected graphs 586
Updated R total:  945020.0
Previous number of connected graphs 585
Updated R total:  943072.0
Previous number of connected graphs 584
Updated R total:  941126.0
Previous number of connected graphs 583
Updated R total:  939154.0
Previous number of connected graphs 582
Updated R total:  937203.0
Previous number of connected graphs 581
Updated R total:  935242.0
Previous number of connected graphs 580
Updated R total:  933302.0
Previous number of connected graphs 579
Updated R total:  931283.0
Previous number of connected graphs 578
Updated R total:  929347.0
Previous number of connected graphs

Previous number of connected graphs 468
Updated R total:  720769.0
Previous number of connected graphs 467
Updated R total:  719120.0
Previous number of connected graphs 466
Updated R total:  717403.0
Previous number of connected graphs 465
Updated R total:  715695.0
Previous number of connected graphs 464
Updated R total:  713989.0
Previous number of connected graphs 463
Updated R total:  712283.0
Previous number of connected graphs 462
Updated R total:  710579.0
Previous number of connected graphs 461
Updated R total:  708237.0
Previous number of connected graphs 460
Updated R total:  706538.0
Previous number of connected graphs 459
Updated R total:  704844.0
Previous number of connected graphs 458
Updated R total:  693872.0
Previous number of connected graphs 457
Updated R total:  692181.0
Previous number of connected graphs 456
Updated R total:  690501.0
Previous number of connected graphs 455
Updated R total:  688683.0
Previous number of connected graphs 454
Updated R total:  6868

Updated R total:  464899.0
Previous number of connected graphs 345
Updated R total:  462064.0
Previous number of connected graphs 344
Updated R total:  460598.0
Previous number of connected graphs 343
Updated R total:  459137.0
Previous number of connected graphs 342
Updated R total:  457970.0
Previous number of connected graphs 341
Updated R total:  456264.0
Previous number of connected graphs 340
Updated R total:  454805.0
Previous number of connected graphs 339
Updated R total:  453348.0
Previous number of connected graphs 338
Updated R total:  451944.0
Previous number of connected graphs 337
Updated R total:  450492.0
Previous number of connected graphs 336
Updated R total:  449094.0
Previous number of connected graphs 335
Updated R total:  447104.0
Previous number of connected graphs 334
Updated R total:  445650.0
Previous number of connected graphs 333
Updated R total:  444015.0
Previous number of connected graphs 332
Updated R total:  442386.0
Previous number of connected graphs

Updated R total:  243705.0
Previous number of connected graphs 222
Updated R total:  242163.0
Previous number of connected graphs 221
Updated R total:  239505.0
Previous number of connected graphs 220
Updated R total:  238609.0
Previous number of connected graphs 219
Updated R total:  236593.0
Previous number of connected graphs 218
Updated R total:  235379.0
Previous number of connected graphs 217
Updated R total:  233519.0
Previous number of connected graphs 216
Updated R total:  232231.0
Previous number of connected graphs 215
Updated R total:  230546.0
Previous number of connected graphs 214
Updated R total:  229335.0
Previous number of connected graphs 213
Updated R total:  227331.0
Previous number of connected graphs 212
Updated R total:  225071.0
Previous number of connected graphs 211
Updated R total:  223871.0
Previous number of connected graphs 210
Updated R total:  222673.0
Previous number of connected graphs 209
Updated R total:  221147.0
Previous number of connected graphs

Updated R total:  74587.0
Previous number of connected graphs 99
Updated R total:  73541.0
Previous number of connected graphs 98
Updated R total:  72499.0
Previous number of connected graphs 97
Updated R total:  71593.0
Previous number of connected graphs 96
Updated R total:  70322.0
Previous number of connected graphs 95
Updated R total:  69057.0
Previous number of connected graphs 94
Updated R total:  66990.0
Previous number of connected graphs 93
Updated R total:  65949.0
Previous number of connected graphs 92
Updated R total:  65355.0
Previous number of connected graphs 91
Updated R total:  64321.0
Previous number of connected graphs 90
Updated R total:  63363.0
Previous number of connected graphs 89
Updated R total:  62335.0
Previous number of connected graphs 88
Updated R total:  61451.0
Previous number of connected graphs 87
Updated R total:  58879.0
Previous number of connected graphs 86
Updated R total:  57929.0
Previous number of connected graphs 85
Updated R total:  56981.0